In [7]:
import pandas as pd
import numpy as np
import os
from tqdm import tqdm

# Paso 1: Cargar todos los datasets

Cargamos todos los archivos CSV necesarios en DataFrames de pandas.

In [2]:
print("Cargando datasets...")
try:
    # Cargar los datos de ferroaleaciones
    df_ferro = pd.read_csv('files/original/ferro.csv')

    # Cargar los archivos de datos del proceso
    df_basket = pd.read_csv('files/processed/df_basket_charged.csv')
    df_eaf_added = pd.read_csv('files/processed/eaf_added_materials_preprocessed.csv')
    df_tapping = pd.read_csv('files/processed/ladle_tapping_converted.csv')
    df_transformer = pd.read_csv('files/processed/eaf_transformer_preprocessed.csv')
    df_temp = pd.read_csv('files/processed/eaf_temp_preprocessed.csv')
    df_gas = pd.read_csv('files/processed/eaf_gaslance_mat_converted.csv') # Usando muestra, reemplazar si se tiene el completo
    df_carbon = pd.read_csv('files/processed/inj_mat_converted.csv') # Usando muestra, reemplazar si se tiene el completo

    print("Todos los datasets se cargaron correctamente.")
except FileNotFoundError as e:
    print(f"Error cargando archivos: {e}. Asegúrate de que todos los CSV estén en la misma carpeta.")

Cargando datasets...
Todos los datasets se cargaron correctamente.


# Paso 2. Preprocesamiento y Estandarizacion de Datos.

- Convertir todas las columnas de tiempo al formato 'datetime'
- Limpiar y preparar `ferro.csv` para poder vincularlo con las adiciones de material.
- Estandarizamos las columnas de los archivos de adición de materiales para poder unirlos.

In [3]:
print("\nPreprocesando y estandarizando datos...")

def to_datetime(df, column_name):
    df[column_name] = pd.to_datetime(df[column_name], errors='coerce')
    return df

# Limpiar y preparar datos de ferroaleaciones
df_ferro = df_ferro.set_index('MAT_CODE').fillna(0)
chem_elements = [col for col in df_ferro.columns if col.isupper() and len(col) <= 2]
df_ferro = df_ferro[chem_elements]

def process_material_additions(df, amount_col, time_col):
    df = to_datetime(df, time_col).rename(columns={time_col: 'Timestamp'})
    # Asegurarse de que la columna de cantidad sea numérica
    df[amount_col] = pd.to_numeric(df[amount_col], errors='coerce')
    df_chem = df.join(df_ferro, on='MAT_CODE')
    for element in chem_elements:
        df_chem[element] = df_chem[amount_col] * (df_chem[element] / 100.0)
    
    df_chem = df_chem[['HEATID', 'Timestamp', amount_col] + chem_elements]
    df_chem = df_chem.rename(columns={amount_col: 'Total_Material_Added'})
    return df_chem

all_materials = pd.concat([
    process_material_additions(df_basket, 'CHARGED_AMOUNT', 'DATETIME'),
    process_material_additions(df_eaf_added, 'CHARGE_AMOUNT', 'DATETIME'),
    process_material_additions(df_tapping, 'CHARGE_AMOUNT', 'DATETIME')
])

# Estandarizar las otras fuentes de datos
df_transformer = to_datetime(df_transformer, 'STARTTIME').rename(columns={'STARTTIME': 'Timestamp'})
df_temp = to_datetime(df_temp, 'DATETIME').rename(columns={'DATETIME': 'Timestamp'})
df_gas = to_datetime(df_gas, 'REVTIME').rename(columns={'REVTIME': 'Timestamp'})
df_carbon = to_datetime(df_carbon, 'REVTIME').rename(columns={'REVTIME': 'Timestamp'})

# Calcular tasa de cambio para datos acumulativos (gas y carbón)
for df in [df_gas, df_carbon]:
    for col in df.columns:
        if df[col].dtype == 'object' and col != 'HEATID':
            df[col] = pd.to_numeric(df[col].astype(str).str.replace(',', '.'), errors='coerce')
df_gas['O2_used'] = df_gas.groupby('HEATID')['O2_AMOUNT'].diff().fillna(0)
df_gas['GAS_used'] = df_gas.groupby('HEATID')['GAS_AMOUNT'].diff().fillna(0)
df_carbon['Carbon_used'] = df_carbon.groupby('HEATID')['INJ_AMOUNT_CARBON'].diff().fillna(0)

# --- CAMBIO CLAVE: Usamos .agg() para ser explícitos y evitar errores de tipo ---
print("Pre-agregando datos para eliminar duplicados de índice de forma segura...")

# Definimos las columnas numéricas para cada dataframe
numeric_cols_materials = ['Total_Material_Added'] + chem_elements
numeric_cols_transformer = ['TAP', 'MW', 'MW_scaled']
numeric_cols_temp = ['TEMP', 'VALO2_PPM', 'VALO2_PPM_no_cero', 'VALO2_PPM_transformado', 'TEMP_transformado']
numeric_cols_gas = ['O2_AMOUNT', 'GAS_AMOUNT', 'O2_FLOW', 'GAS_FLOW', 'O2_used', 'GAS_used']
numeric_cols_carbon = ['INJ_AMOUNT_CARBON', 'INJ_FLOW_CARBON', 'Carbon_used']

# Aplicamos la agregación solo a las columnas numéricas correspondientes
all_materials = all_materials.groupby(['HEATID', 'Timestamp'])[numeric_cols_materials].sum().reset_index()
df_transformer = df_transformer.groupby(['HEATID', 'Timestamp'])[numeric_cols_transformer].mean().reset_index()
df_temp = df_temp.groupby(['HEATID', 'Timestamp'])[numeric_cols_temp].mean().reset_index()
df_gas = df_gas.groupby(['HEATID', 'Timestamp'])[numeric_cols_gas].sum().reset_index()
df_carbon = df_carbon.groupby(['HEATID', 'Timestamp'])[numeric_cols_carbon].sum().reset_index()
# ----------------------------------------------------------------------------------

print("Estandarización y manejo de duplicados completado.")


Preprocesando y estandarizando datos...
Pre-agregando datos para eliminar duplicados de índice de forma segura...
Estandarización y manejo de duplicados completado.


# Paso 3. Consolidar datos para un solo `HEATID`

- Elegimos un `HEATID` como ejemplo
- Filtramos todos los dataframes para obtener solo los datos de ese `HEATID`
- Calculamos la tasa de cambio para los datos acumulativos (gas y carbon).

(Esto solo lo haremos para la prueba inicial)

In [4]:
print("\nIniciando la consolidación para todos los HEATIDs...")

# Preparar cada DataFrame con el índice correcto ANTES de unirlos
all_materials.set_index(['HEATID', 'Timestamp'], inplace=True)
df_transformer.set_index(['HEATID', 'Timestamp'], inplace=True)
df_temp.set_index(['HEATID', 'Timestamp'], inplace=True)
df_gas.set_index(['HEATID', 'Timestamp'], inplace=True)
df_carbon.set_index(['HEATID', 'Timestamp'], inplace=True)

# Unimos todo usando un outer join para no perder datos.
# Ahora todas las tablas tienen el mismo tipo de índice (MultiIndex)
df_merged = pd.concat(
    [all_materials, df_transformer, df_temp, df_gas, df_carbon], 
    axis=1, 
    join='outer'
)

df_merged.reset_index(inplace=True)
df_merged.sort_values(by=['HEATID', 'Timestamp'], inplace=True)

print("Consolidación inicial completada.")


Iniciando la consolidación para todos los HEATIDs...
Consolidación inicial completada.


# Paso 4: Re-muestreo y Agregación
- Creamos un `DataFrame` maestro con un índice de tiempo de frecuencia fija (1 minuto).

- Agregamos los datos de cada fuente a este intervalo de 1 minuto.
    - **Adiciones:** Suma total por minuto.
    - **Transformador:** Potencia promedio y TAP máximo.
    - **Inyecciones:** Uso total y flujo promedio.
    - **Temperatura:** Propagamos el último valor conocido (`ffill`).

In [8]:
print("Re-muestreando y agregando datos a una frecuencia de 1 minuto para cada HEATID...")
grouped = df_merged.groupby('HEATID')
all_heats_resampled = []

for heat_id, group in tqdm(grouped, desc="Procesando HEATIDs"):
    group = group.set_index('Timestamp').sort_index()
    
    # Definir las operaciones de agregación
    agg_operations = {
        'Total_Material_Added': 'sum', 'MW': 'mean', 'TAP': 'max',
        'O2_used': 'sum', 'GAS_used': 'sum', 'O2_FLOW': 'mean', 'GAS_FLOW': 'mean',
        'Carbon_used': 'sum', 'INJ_FLOW_CARBON': 'mean',
        'TEMP': 'mean', 'VALO2_PPM': 'mean'
    }
    for element in chem_elements:
        if element in group.columns:
            agg_operations[element] = 'sum'
            
    resampled_group = group.resample('1T').agg(agg_operations)
    
    # Propagar mediciones dispersas (forward fill)
    resampled_group[['TEMP', 'VALO2_PPM']] = resampled_group[['TEMP', 'VALO2_PPM']].ffill()
    
    resampled_group['HEATID'] = heat_id
    all_heats_resampled.append(resampled_group)

df_final = pd.concat(all_heats_resampled)
df_final.reset_index(inplace=True)
df_final.fillna(0, inplace=True)
print("Re-muestreo y agregación completados.")

Re-muestreando y agregando datos a una frecuencia de 1 minuto para cada HEATID...


Procesando HEATIDs:   0%|          | 0/20827 [00:00<?, ?it/s]C:\Users\rprie\AppData\Local\Temp\ipykernel_3760\2662431323.py:19: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  resampled_group = group.resample('1T').agg(agg_operations)
Procesando HEATIDs:   0%|          | 1/20827 [00:00<4:03:24,  1.43it/s]C:\Users\rprie\AppData\Local\Temp\ipykernel_3760\2662431323.py:19: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  resampled_group = group.resample('1T').agg(agg_operations)
C:\Users\rprie\AppData\Local\Temp\ipykernel_3760\2662431323.py:19: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  resampled_group = group.resample('1T').agg(agg_operations)
C:\Users\rprie\AppData\Local\Temp\ipykernel_3760\2662431323.py:19: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  resampled_group

Re-muestreo y agregación completados.


# Paso 5: Unir en un DataFrame Final y Guardar
 
- Unimos todos los dataframes re-muestreados en el `DataFrame` maestro.
- Rellenamos los valores nulos restantes.
- Guardamos el resultado en un nuevo archivo CSV.

In [10]:
output_filename = 'all_heats_consolidated.csv'
df_final.to_csv(output_filename, index=False)

print(f"\n¡Proceso completado! Todos los datos han sido consolidados.")
print(f"Archivo guardado como: {output_filename}")
print("\n--- Vista Previa del DataFrame Final ---")
print(df_final.head())
print(f"\nDimensiones del DataFrame final: {df_final.shape}")
print(f"Número de HEATIDs únicos procesados: {df_final['HEATID'].nunique()}")


¡Proceso completado! Todos los datos han sido consolidados.
Archivo guardado como: all_heats_consolidated.csv

--- Vista Previa del DataFrame Final ---
            Timestamp  Total_Material_Added   MW  TAP  O2_used  GAS_used  \
0 2015-01-01 00:50:00                   0.0  0.0  0.0  -3796.0   -1141.0   
1 2015-01-01 00:51:00               76751.0  0.0  0.0      9.0       1.0   
2 2015-01-01 00:52:00                   0.0  0.0  0.0     37.0      19.0   
3 2015-01-01 00:53:00                   0.0  0.0  0.0     42.0      20.0   
4 2015-01-01 00:54:00                   0.0  0.0  0.0     42.0      20.0   

       O2_FLOW     GAS_FLOW  Carbon_used  INJ_FLOW_CARBON  TEMP  VALO2_PPM  \
0     0.000000     0.000000          0.0              0.0   0.0        0.0   
1   863.166667   318.166667          0.0              0.0   0.0        0.0   
2  2291.000000  1177.333333      -1051.0              0.0   0.0        0.0   
3  2480.000000  1187.500000          0.0              0.0   0.0        0.0   
